## How to get csv files for analysis below
- Make sure your shells pwd is this directory
- Connect to an analytics database
- Run csv export (adjust the timestamp filter first)
  ```psql
  \copy (select * from areaoccupancy a join metadata m on m.id = a.metadata_id where a.occupancy_time > '2025-12-10' order by a.occupancy_time) to 'tsp-area.csv' with csv header
  \copy (select * from linecrossing l join metadata m on m.id = l.metadata_id where l.crossing_time > '2025-12-10' order by l.crossing_time) to 'tsp-line.csv' with csv header
  ```

In [57]:
# Read tsp-area.csv with pandas and output a list of areas
import pandas as pd
from pathlib import Path


def read_area_csv(file: Path) -> pd.DataFrame:
    FILTER_AREAS = [
        'parking-meckauer-west01',
        'parking-meckauer-west02',
        'parking-meckauer-west03',
        'parking-meckauer-center',
        'parking-meckauer-center02',
        'parking-meckauer-ost01',
        'parking-meckauer-ost02',
    ]

    area_df = pd.read_csv(file)
    # Drop all uninteresting columns
    area_df = area_df[['occupancy_time', 'name', 'count']]
    area_df['occupancy_time'] = pd.to_datetime(area_df['occupancy_time'], format='ISO8601')
    area_df = area_df.loc[area_df['name'].isin(FILTER_AREAS)]

    # Create time buckets by flooring the time value
    area_df['occupancy_time_buckets'] = area_df['occupancy_time'].dt.floor('10s')

    # Pivot area names into columns and sum
    pivoted_area_df = area_df.pivot_table(values='count', index='occupancy_time_buckets', columns='name', aggfunc='mean')
    pivoted_area_df['total_count'] = pivoted_area_df.sum(axis=1)

    return pivoted_area_df

def read_line_csv(file: Path) -> pd.DataFrame:
    line_df = pd.read_csv('tsp-line.csv')
    line_df = line_df[['crossing_time', 'name', 'direction']]
    line_df = line_df.loc[line_df['name'] == 'flow-meckauer-main']
    return line_df

In [91]:
def simple_counting(line_df: pd.DataFrame) -> pd.DataFrame:
    results = []
    count = 0
    for crossing in line_df.itertuples():
        if crossing.direction == 'in':
            count += 1
        else:
            count -= 1
        results.append([crossing.crossing_time, count])
    return pd.DataFrame(columns=['flow_occupancy_time', 'count'], data=results)

def lower_bounded_counting(line_df: pd.DataFrame) -> pd.DataFrame:
    results = []
    count = 0
    for crossing in line_df.itertuples():
        if crossing.direction == 'in':
            count += 1
        else:
            count = max(0, count - 1)
        results.append([crossing.crossing_time, count])
    return pd.DataFrame(columns=['flow_occupancy_time', 'count'], data=results)

def bounded_counting(line_df: pd.DataFrame, upper_bound: int) -> pd.DataFrame:
    results = []
    count = 0
    for crossing in line_df.itertuples():
        if crossing.direction == 'in':
            count = min(upper_bound, count + 1)
        else:
            count = max(0, count - 1)
        results.append([crossing.crossing_time, count])
    return pd.DataFrame(columns=['flow_occupancy_time', 'count'], data=results)

In [93]:
staging_area_df = read_area_csv('tsp-area.csv')
dev_area_df = read_area_csv('dev-area.csv')

staging_flow_df_simple = simple_counting(read_line_csv('tsp_Line.csv'))
staging_flow_df_lower_bounded = lower_bounded_counting(read_line_csv('tsp_Line.csv'))
staging_flow_df_bounded = bounded_counting(read_line_csv('tsp_Line.csv'), upper_bound=75)

In [94]:
import plotly.graph_objects as go

fig = go.Figure()

fig.add_trace(
    go.Scattergl(
        x=staging_area_df.index, 
        y=staging_area_df['total_count'],
        mode='lines',        # or "lines+markers"
        name='area_occupancy (ground truth)'
    ),
)

def add_algo_result(df: pd.DataFrame, name: str):
    fig.add_trace(
        go.Scattergl(
            x=df['flow_occupancy_time'], 
            y=df['count'],
            mode='lines',        # or "lines+markers"
            name=name
        ),
    )


add_algo_result(staging_flow_df_simple, 'simple counting')
add_algo_result(staging_flow_df_lower_bounded, 'lower bounded counting')
add_algo_result(staging_flow_df_bounded, 'bounded counting (UB=75)')

fig.update_layout(
    title='Count over Time',
    xaxis_title='time',
    yaxis_title='total_count',
)

fig.show()